In [ ]:
import pandas as pd
import pickle
import random

import numpy as np
import torch
#import ninja
from backend.disentangle_concepts import *
import dnnlib 
import legacy

%load_ext autoreload
%autoreload 2

annotations_file = './data/annotated_files/seeds0000-50000.pkl'
with open(annotations_file, 'rb') as f:
    annotations = pickle.load(f)

ann_df = pd.read_csv('./data/annotated_files/sim_seeds0000-50000.csv')
concepts = './data/concepts.txt'

with open(concepts) as f:
    labels = [line.strip() for line in f.readlines()]

with dnnlib.util.open_url('./data/model_files/network-snapshot-010600.pkl') as f:
    model = legacy.load_network_pkl(f)['G_ema'].to('cpu') # type: ignore


In [ ]:
concept_id = 'Abstract'
separation_vector, number_important_features, important_nodes, accuracy_sep = get_separation_space(concept_id, annotations, ann_df, method='LR', samples=150, C=0.1, latent_space='W')

In [ ]:
separation_vector.shape

In [ ]:
# get_verification_score(concept_id, separation_vector, model, annotations)

In [ ]:
print(number_important_features, important_nodes)

In [ ]:
seed = random.randint(0,10000)
original_image_vec = annotations['w_vectors'][seed]
img = generate_original_image(original_image_vec, model, latent_space='W')
img

In [ ]:
images, lambdas = regenerate_images(model, original_image_vec, separation_vector, min_epsilon=-(int(10)), max_epsilon=int(10), latent_space='W')

In [ ]:
images[0]

In [ ]:
images[-1]

In [ ]:
import open_clip
import os
import random
from tqdm import tqdm
os.environ["CUDA_VISIBLE_DEVICES"] = ""

model_clip, _, preprocess = open_clip.create_model_and_transforms('ViT-L-14', pretrained='laion2b_s32b_b82k')
tokenizer = open_clip.get_tokenizer('ViT-L-14')

pre_prompt = "Artwork, " #@param {type:"string"}
text_descriptions = [f"{pre_prompt}{label}" for label in labels]
text_tokens = tokenizer(text_descriptions)

with torch.no_grad(), torch.cuda.amp.autocast():
    text_features = model_clip.encode_text(text_tokens).float()
    text_features /= text_features.norm(dim=-1, keepdim=True)
    
text_features = text_features.cpu().numpy()
print(text_features.shape)



In [ ]:
import open_clip
import os
import random
from tqdm import tqdm
os.environ["CUDA_VISIBLE_DEVICES"] = ""

In [ ]:
import pandas as pd
import torch

In [ ]:
model_clip, _, preprocess = open_clip.create_model_and_transforms('ViT-L-14', pretrained='laion2b_s32b_b82k')
tokenizer = open_clip.get_tokenizer('ViT-L-14')

labels = []
for type_col in ['Provenance', 'Shape Name', 'Fabric', 'Technique']:
    ann_df = pd.read_csv(f'./data/vase_annotated_files/sim_{type_col}_seeds0000-20000.csv').drop(['Unnamed: 0', 'ID'], axis=1)
    
    labels += [type_col + ' ' + lbl for lbl in list(ann_df.columns)]
        
print(labels)
pre_prompt = "Vase art, " #@param {type:"string"}
text_descriptions = [f"{pre_prompt}{label}" for label in labels]
text_tokens = tokenizer(text_descriptions)

with torch.no_grad(), torch.cuda.amp.autocast():
    text_features = model_clip.encode_text(text_tokens).float()
    text_features /= text_features.norm(dim=-1, keepdim=True)
    
text_features = text_features.cpu().numpy()
print(text_features.shape)

In [ ]:
dic_clip_vecs = {l:v for l,v in zip(labels, text_features)}

In [ ]:
import pickle

In [ ]:
dic_clip_vecs['Provenance ADRIA'].shape
with open('data/CLIP_vecs_vases.pkl', 'wb') as f:
    pickle.dump(dic_clip_vecs, f)

In [ ]:
dic_clip_vecs['Abstract'].shape
with open('data/CLIP_vecs.pkl', 'wb') as f:
    pickle.dump(dic_clip_vecs, f)

In [ ]:
with open(annotations_file, 'rb') as f:
        annotations = pickle.load(f)
annotations['fname'][:10], annotations['z_vectors'][:1],# annotations['annotations'][:5]

In [ ]:
seed = random.randint(0,10000)
original_image_vec = annotations['z_vectors'][seed]
img = generate_original_image(original_image_vec, model)

In [ ]:
concept_id = "Readymade"

In [ ]:
samples = 500 
abstracts = np.array([float(ann) for ann in ann_df[concept_id]])

repr_idxs = list(np.argsort(abstracts))[:samples]
abstract_idxs = list(np.argsort(abstracts))[-samples:]
    
z = annotations['z_vectors'][abstract_idxs[0]]
img = generate_original_image(z, model)
if 'ID' in ann_df.columns:
    ann_df = ann_df.drop('ID', axis=1)
print(ann_df.loc[abstract_idxs[0], :].sort_values()[-20:])
img

In [ ]:
ann_df['Abstract'].value_counts()

In [ ]:
z = annotations['z_vectors'][repr_idxs[0]]
img = generate_original_image(z, model)
print(ann_df.loc[repr_idxs[0], :].sort_values())
img

In [ ]:
for col in ann_df.columns:
    if '1' in col:
        print(col)

In [ ]:
concepts = ['Op Art', 'Minimalism', 'Surrealism', 'Baroque', 'Lithography', 'Woodcut', 'Etching', 'Intaglio',]

vectors, nodes_in_common = get_concepts_vectors(concepts, annotations, ann_df, method='LR', samples=150, C=0.1)

In [ ]:
print(nodes_in_common)

In [ ]:
# import plotly.graph_objects as go

# # Generate example data
# x = projection[:, 0]  # x-coordinates of vectors
# y = projection[:, 1]  # y-coordinates of vectors
# z = projection[:, 2]  # z-coordinates of vectors
# data = []

# for i in range(len(x)):
#     # Create a 3D scatter plot
#     data.append(go.Scatter3d(
#         x=[0, x[i]],  # Start at x = 0
#         y=[0, y[i]],  # Start at y = 0
#         z=[0, z[i]],  # Start at z = 0
#         mode='lines',
#         marker=dict(size=5),
#         line=dict(width=2),
#         hovertext=concepts[i],
#         text=concepts[i],
#         name=concepts[i],
#         showlegend=True,
#     ))

# # layout = go.Layout(margin = dict( l = 0,
# #                                   r = 0,
# #                                   b = 0,
# #                                   t = 0)
# #                   )
# fig = go.Figure(data=data)
# # plot(fig,filename="vector.html",auto_open=False,image='png',image_height=800,image_width=1500)
# # # Set the title
# fig.update_layout(title='3D Vectors')
# # Set the axis labels
# fig.update_layout(scene=dict(
#     xaxis=dict(title='X', range=[-10, 10],),
#     yaxis=dict(title='Y', range=[-10, 10],),
#     zaxis=dict(title='Z', range=[-10, 10],),
# ))

# # Show the plot
# fig.show()


In [ ]:
from sklearn.metrics.pairwise import cosine_similarity

edges = []
for i in range(len(concepts)):
    for j in range(len(concepts)):
        if i != j:
            print(f'Similarity between {concepts[i]} and {concepts[j]}')
            similarity = cosine_similarity(vectors[i,:].reshape(1, -1), vectors[j,:].reshape(1, -1))
            print(np.round(similarity[0][0], 3))
            edges.append((concepts[i], concepts[j], np.round(similarity[0][0], 3)))


In [ ]:
import matplotlib.pyplot as plt
import networkx as nx

In [ ]:
# Create an empty graph
G = nx.Graph()

# Add edges with weights to the graph
for edge in edges:
    node1, node2, weight = edge
    G.add_edge(node1, node2, weight=weight)

# Draw the graph
pos = nx.spring_layout(G)  # Position nodes using the spring layout algorithm
nx.draw_networkx(G, pos=pos, with_labels=True, node_color='lightblue', node_size=500, font_size=12)

# Draw edge labels with weights
edge_labels = nx.get_edge_attributes(G, 'weight')
nx.draw_networkx_edge_labels(G, pos=pos, edge_labels=edge_labels)

# Display the graph interactively
plt.axis('off')
plt.show()

In [ ]:
import nxviz as nv


In [ ]:
from pyvis.network import Network

In [ ]:
net = Network(notebook=True, height="750px", width="100%",)
for e in edges:
    src = e[0]
    dst = e[1]
    w = e[2]

    net.add_node(src, src, title=src)
    net.add_node(dst, dst, title=dst)
    net.add_edge(src, dst, value=w, title=src + ' to ' + dst + ' similarity ' +str(w))
print(net)

# neighbor_map = net.get_adj_list()

# # add neighbor data to node hover data
# for node in net.nodes:
#     node["title"] += " Neighbors:<br>" + "<br>".join(neighbor_map[node["id"]])
#     node["value"] = len(neighbor_map[node["id"]])


# net.toggle_physics(True)
net.show('nx.html')

In [ ]:
# seed = random.randint(0,10000)
# original_image_vec = annotations['z_vectors'][seed]
# img = generate_original_image(original_image_vec, model)

In [ ]:
# z_0 = original_image_vec + 2 * vectors[0] + 2 * vectors[1]
        

In [ ]:
# img = model(z_0.to(), None, truncation_psi=0.7, noise_mode='const')
# img = (img.permute(0, 2, 3, 1) * 127.5 + 128).clamp(0, 255).to(torch.uint8)
        

In [ ]:
with dnnlib.util.open_url('./data/model_files/network-snapshot-010600.pkl') as f:
    G = legacy.load_network_pkl(f)['G_ema'].to('cpu') # type: ignore

In [ ]:
print(G)

In [ ]:
print(G.mapping)

In [ ]:
W = G.mapping(z, None, truncation_psi=0.7)

In [ ]:
print(G.mapping(z, None, truncation_psi=1).shape)

In [ ]:
print(G.synthesis(W, noise_mode='const').shape)

In [ ]:
seed = random.randint(0, 1000000)
W_0 = torch.from_numpy(np.random.RandomState(seed).randn(1, G.z_dim)).to('cpu')
W = W_0.repeat([1, G.num_ws, 1])
img = G.synthesis(W, noise_mode='random')
img = (img.permute(0, 2, 3, 1) * 127.5 + 128).clamp(0, 255).to(torch.uint8)
im = PIL.Image.fromarray(img[0].cpu().numpy(), 'RGB')
im.show()

In [ ]:
z = torch.from_numpy(np.random.RandomState(seed).randn(1, G.z_dim)).to('cpu')
W = G.mapping(z, None, truncation_psi=1)
print(W[0, 0] == W[0, 1])
img = G.synthesis(W, noise_mode='random')
img = (img.permute(0, 2, 3, 1) * 127.5 + 128).clamp(0, 255).to(torch.uint8)
im = PIL.Image.fromarray(img[0].cpu().numpy(), 'RGB')
im.show()

In [ ]:
W[:,0,:,].shape

In [ ]:
z.shape

In [ ]:
z_vals = []
w_vals = []
fnames = []
# Generate images.
seeds = range(100)
for seed_idx, seed in enumerate(seeds):
    print('Generating image for seed %d (%d/%d) ...' % (seed, seed_idx, len(seeds)))
    z = torch.from_numpy(np.random.RandomState(seed).randn(1, G.z_dim))
    z_vals.append(z)
    z = z.to('cpu')
    fnames.append(f'data/images/seed{seed:04d}.png')
    # Construct an inverse rotation/translation matrix and pass to the generator.  The
    # generator expects this matrix as an inverse to avoid potentially failing numerical
    # operations in the network.
    # if hasattr(G.synthesis, 'input'):
    #     m = make_transform(translate, rotate)
    #     m = np.linalg.inv(m)
    #     G.synthesis.input.transform.copy_(torch.from_numpy(m))
    W = G.mapping(z, None, truncation_psi=1)
    w_vals.append(W[:,0,:])
    img = G.synthesis(W, noise_mode='const')

    #img = G(z, None, truncation_psi=0.7, noise_mode='const')
    img = (img.permute(0, 2, 3, 1) * 127.5 + 128).clamp(0, 255).to(torch.uint8)
    PIL.Image.fromarray(img[0].cpu().numpy(), 'RGB').save(f'data/images/seed{seed:04d}.png')
    
info = {'fname': fnames, 'z_vectors': z_vals, 'w_vectors': w_vals}
with open(f'data/images/seeds{seeds[0]:04d}-{seeds[-1]:04d}.pkl', 'wb') as f:
    pickle.dump(info, f)


In [ ]:
# import open_clip
# from open_clip import tokenizer

In [ ]:
# model, _, preprocess = open_clip.create_model_and_transforms('ViT-g-14', pretrained='laion2b_s34b_b88k')
# print(model.eval())
# context_length = model.context_length
# vocab_size = model.vocab_size


In [ ]:
import rdflib
import csv

# Load the RDF file
rdf_file = '/Users/ludovicaschaerf/Desktop/Vase data/Getty vases.rdf'
graph = rdflib.Graph()
graph.parse(rdf_file)

# Specify the desired CSV file path
csv_file = '/Users/ludovicaschaerf/Desktop/Vase data/Getty vases.csv'
print(len(graph))

In [ ]:
print(len(graph))

In [ ]:
# Open the CSV file in write mode
with open(csv_file, 'w', newline='', encoding='utf-8') as file:

    # Create a CSV writer object
    writer = csv.writer(file)

    # Write the header row
    writer.writerow(['Subject', 'Predicate', 'Object'])

    # Iterate over each triple in the RDF graph
    for subject, predicate, obj in graph:

        # Convert the triple components to strings
        subject_str = str(subject)
        predicate_str = str(predicate)
        object_str = str(obj)

        # Write the triple as a row in the CSV file
        writer.writerow([subject_str, predicate_str, object_str])

print('Conversion completed successfully!')


In [ ]:
import pandas as pd
final_file = pd.read_csv(csv_file)
final_file

In [ ]:
vases = pd.read_csv('/Users/ludovicaschaerf/Desktop/Vase data/oxford_vases_info.csv')
vases_links = vases['URI']
vases.head()

In [ ]:
vases['Vase Number'].nunique(), vases.shape

In [ ]:
vases = vases.groupby('Vase Number').first().reset_index()

In [ ]:
from bs4 import BeautifulSoup
import requests
response = requests.get(vases_links[0])
html_content = response.text
soup = BeautifulSoup(html_content, 'html.parser')
div = soup.find('div', class_='recordImage')
if div is not None:
    img = div.find('img')
    if img is not None:
        img_src = img['src']
        print("Image source:", img_src)
    else:
        print("No image found inside the div.")
else:
    print("Div not found.")

In [ ]:
import os
# Specify the folder path to save the images
folder_path = '/Users/ludovicaschaerf/Desktop/Vase data/images'

# Create the folder if it doesn't exist
os.makedirs(folder_path, exist_ok=True)

In [ ]:
from tqdm import tqdm

In [ ]:
for uri,i in tqdm(zip(vases['URI'], vases['Vase Number'])):
    if i > 473:
        response = requests.get(uri)
        html_content = response.text
        soup = BeautifulSoup(html_content, 'html.parser')
        div = soup.find('div', class_='recordImage')
        if div is not None:
            img = div.find('img')
            if img is not None:
                img_src = 'https://www.carc.ox.ac.uk/' + img['src']
                print("Image source:", img_src)
            else:
                print("No image found inside the div.", i)
                continue
        else:
            print("Div not found.", i)
            continue
        # Specify the path to save the image
        save_path = os.path.join(folder_path, str(i) + '.jpg')

        # Download the image and save it to the specified path
        response = requests.get(img_src)
        if response.status_code == 200:
            with open(save_path, 'wb') as file:
                file.write(response.content)
            print("Image downloaded successfully.")
        else:
            print("Failed to download the image.")
            continue